### Setup

In [5]:
import os
import io
import json
import base64
import requests
import concurrent.futures
import time
from IPython.display import display, Markdown, Latex

import shapely

import numpy as np
import pandas as pd

import vertexai
from vertexai.preview.language_models import TextGenerationModel, TextEmbeddingModel, ChatModel
from google.cloud import aiplatform
from google.cloud import storage
from google.cloud import bigquery


In [6]:
project = !gcloud config get-value project
PROJECT_ID = project[0]
PROJECT_ID

'mg-ce-demos'

In [7]:
REGION = 'us-central1'
LOCATION = 'us'
GCS_BUCKET = PROJECT_ID

In [8]:
#speech client
#stt = speech.SpeechClient()

# gcs client
gcs = storage.Client(project = PROJECT_ID)

# vertex ai clients
vertexai.init(project = PROJECT_ID, location = REGION)
aiplatform.init(project = PROJECT_ID, location = REGION)

# bigquery client
bq = bigquery.Client(project = PROJECT_ID)

### Get audio files
Need to loop through all files in a GCS bucket

In [9]:
bucket = gcs.bucket(GCS_BUCKET)

# Get the list of blobs
blobs = bucket.list_blobs()

# Loop through the blobs
mp3_data = []
for blob in blobs:
    if blob.name.startswith('audio_data/test'):
        if blob.name.endswith('.mp3'):
            #print(blob.name)
            mp3_data.append([blob.name, blob.content_type, f'gs://{GCS_BUCKET}/{blob.name}'])
            
mp3_data

[['audio_data/test/Mapping_uncharted_undersea_volcanoes,_and_elephant_seals_dive_deep_to_sleep.mp3',
  'audio/mpeg',
  'gs://mg-ce-demos/audio_data/test/Mapping_uncharted_undersea_volcanoes,_and_elephant_seals_dive_deep_to_sleep.mp3']]

In [10]:
#example_audio_uri = "speech/brooklyn_bridge.flac"
#example_audio_uri2 = "speech/sample-podcasts/GCPEpisode328-DatabaseMigrationService-2min sample.flac"
#example_audio_uri3 = "speech/multi.wav"

#gcs_bucket = 'cloud-samples-data'
#bucket = gcs.bucket(gcs_bucket)
#blob = bucket.blob(example_audio_uri2)

#audio_bytes = blob.download_as_bytes()

In [11]:
#gcs_uri = "gs://cloud-samples-data/speech/sample-podcasts/GCPEpisode328-DatabaseMigrationService-2min sample.flac"

In [12]:
#type(audio_bytes)

### STT setup - including multiple speakers

In [13]:
from google.cloud import speech_v1p1beta1 as speech  #v1 has detect different speakers, v2 does not yet
from google.cloud.speech_v1p1beta1 import SpeechClient
from google.cloud.speech_v1p1beta1.types import cloud_speech

def transcribe_gcs(gcs_uri: str) -> str:
    """Asynchronously transcribes the audio file specified by the gcs_uri.

    Args:
        gcs_uri: The Google Cloud Storage path to an audio file.

    Returns:
        The generated transcript from the audio file provided.
    """

    TIMEOUT_DEFAULT = 3600

    client = SpeechClient()

    audio = cloud_speech.RecognitionAudio(uri=gcs_uri)
    config = cloud_speech.RecognitionConfig(
        encoding=cloud_speech.RecognitionConfig.AudioEncoding.MP3,    # Configure audio file type to MP3
        sample_rate_hertz=44100,                                      # Sampling rate set to 44.1KHz
        language_code="en-US",                                        # Language: U. S. English
        enable_automatic_punctuation=True,                            # Enabled automatic punctuation while transforming
        enable_word_confidence=True,                                  # Enabled confidence scores for transcriptions
        model="latest_long",                                          # Works for most of the audio files including long files over 10 minutes
        diarization_config=cloud_speech.SpeakerDiarizationConfig(     # Enabled speaker diarization
            enable_speaker_diarization=True
        )
    )

    operation = client.long_running_recognize(config=config, audio=audio)   # Execute long running recognition job

    # Please do not decrease the timeout value under 1800 seconds. It can cause timeout error.
    # Most of the podcasts are around 30 minute long and it requires enough timeout value to
    # finish transcription jobs.

    print("Waiting for operation to complete...")

    try:
        response = operation.result(timeout=TIMEOUT_DEFAULT)       # The default is 3600 seconds, 1 hour

    except:
        response = operation.result(timeout=1.5 * TIMEOUT_DEFAULT) # 5400 seconds, 1 hour and 30 minutes

    finally:
        response = operation.result(timeout=2 * TIMEOUT_DEFAULT)   # 7200 seconds, 2 hours

    #print("Building transcriptions...")
    #transcript_builder = []
    # Each result is for a consecutive portion of the audio. Iterate through
    # them to get the transcripts for the entire audio file.
    #for result in response.results:
    #    alternative = result.alternatives[0]

        # The first alternative is the most likely one for this portion.
    #    transcript_builder.append(f"\n{result.alternatives[0].transcript}")
        # transcript_builder.append(f"\nConfidence: {result.alternatives[0].confidence}")

    #transcript = ''.join(transcript_builder)

    #return transcript_builder
    return response

In [14]:
start_time = time.time()

sample_uri = str(mp3_data[0][2])
response = transcribe_gcs(sample_uri)

end_time = time.time()
total_time = (end_time - start_time)/60
print(f'{total_time} minutes')

Waiting for operation to complete...
16.044940567016603 minutes


#### testing

In [11]:
#diarization_config = speech.SpeakerDiarizationConfig(
#    enable_speaker_diarization=True,
#    min_speaker_count=2,
#    max_speaker_count=8,
#)

In [18]:
#config = speech.RecognitionConfig(
#    #encoding=speech.RecognitionConfig.AudioEncoding.FLAC,
#    encoding=speech.RecognitionConfig.AudioEncoding.MP3,
#    audio_channel_count=2,
#    enable_word_confidence=True,
#    enable_automatic_punctuation=True,
#    profanity_filter=True,
#    language_code="en-US",
#    diarization_config=diarization_config,
#)

In [19]:
#audio = speech.RecognitionAudio(content=audio_bytes)
#audio = speech.RecognitionAudio(uri=mp3_data[0][2])

In [ ]:
# Detects speech in the audio file
#operation = stt.long_running_recognize(config=config, audio=audio)

print("Waiting for operation to complete...")
#response = operation.result()

#### work with data

In [15]:
response

results {
  alternatives {
    transcript: "This podcast is supported by the icon school of medicine at Mount Sinai the academic arm of the Mount Sinai health system in New York City and one of America\'s leading research medical schools. What are researchers working on to advance our understanding of the brain and to improve care for such disorders as depression dementia and drug addiction?"
    confidence: 0.97219491
    words {
      start_time {
        nanos: 100000000
      }
      end_time {
        nanos: 300000000
      }
      word: "This"
      confidence: 0.972195446
    }
    words {
      start_time {
        nanos: 300000000
      }
      end_time {
        nanos: 800000000
      }
      word: "podcast"
      confidence: 0.972195446
    }
    words {
      start_time {
        nanos: 800000000
      }
      end_time {
        seconds: 1
        nanos: 400000000
      }
      word: "is"
      confidence: 0.972195446
    }
    words {
      start_time {
        seconds: 1


In [26]:
print(f'{response.total_billed_time.seconds/60} billed minutes')

36.766666666666666 billed minutes


In [27]:
result = response.results[-1]
words_info = result.alternatives[0].words
#result
#words_info

In [48]:
speaker = 1
text = ''
order = 0
transcript = pd.DataFrame(columns=['file', 'order', 'speaker_tag', 'text'])

for word_info in words_info:
    if word_info.confidence >= 0.8:
        if word_info.speaker_tag==speaker:
            text=text+" "+word_info.word
        else:
            transcript.loc[len(transcript.index)] = [sample_uri, order, str('speaker_'+str(speaker)), text] 
            order += 1
            speaker=word_info.speaker_tag
            text=""+word_info.word

transcript.loc[len(transcript.index)] = [sample_uri, order, str('speaker_'+str(speaker)), text]

In [49]:
transcript['text'].replace('', np.nan, inplace=True)
transcript = transcript.dropna() 
transcript

file  order speaker_tag  \
0   gs://mg-ce-demos/audio_data/test/Mapping_uncha...      0   speaker_1   
1   gs://mg-ce-demos/audio_data/test/Mapping_uncha...      1   speaker_2   
2   gs://mg-ce-demos/audio_data/test/Mapping_uncha...      2   speaker_1   
3   gs://mg-ce-demos/audio_data/test/Mapping_uncha...      3   speaker_2   
4   gs://mg-ce-demos/audio_data/test/Mapping_uncha...      4   speaker_1   
..                                                ...    ...         ...   
91  gs://mg-ce-demos/audio_data/test/Mapping_uncha...     91   speaker_1   
92  gs://mg-ce-demos/audio_data/test/Mapping_uncha...     92   speaker_4   
93  gs://mg-ce-demos/audio_data/test/Mapping_uncha...     93   speaker_1   
94  gs://mg-ce-demos/audio_data/test/Mapping_uncha...     94   speaker_4   
95  gs://mg-ce-demos/audio_data/test/Mapping_uncha...     95   speaker_1   

                                                 text  
0    This podcast is supported by the icon school ...  
1                         This is the science podcast  
2   for April 21st. 2023. I'm Sarah crespi first u...  
3                                           seamounts  
4   staff News writer Paul voosin joins me to disc...  
..                                                ...  
91  behavioral therapies can be effective interven...  
92  really surprisingly little I think that's an a...  
93                         Eric your Thoughts, please  
94  behavioral therapies are the Mainstay for addi...  
95  Eric and Paul. It's been a real pleasure havin...  

[96 rows x 4 columns]

### Build prompts for summarization

In [50]:
prompt_context = []

for i, row in transcript.iterrows():
    prompt_context.append("{0}".format(row["text"]))

prompt_context

[" This podcast is supported by the icon school of medicine at Mount Sinai the academic arm of the Mount Sinai health system in New York City and one of America's leading research medical schools. What are researchers working on to advance our understanding of the brain and to improve care for such disorders as depression dementia and drug addiction? To find out we invite you to read a special supplement to Science magazine prepared by icon Mount Sinai in partnership with science. Just visit our website at www.science.org and search for frontiers of medical research -brainscience the icon school of medicine at Mount Sinai. We find a way.",
 'This is the science podcast',
 "for April 21st. 2023. I'm Sarah crespi first up this week. So many",
 'seamounts',
 "staff News writer Paul voosin joins me to discuss a study that nearly the number these submarine volcanoes next up how to mammals that spend 90% of their time in the water at any sleep. Jessica Kendall Barr is here to talk about her 

In [51]:
prompt_context_by_speaker = []

for tag in transcript.speaker_tag.unique():
    prompt_context_temp = []
    for i, row in transcript[transcript.speaker_tag == tag].iterrows():
        prompt_context_temp.append("{0}".format(row["text"]))
    prompt_context_by_speaker.append([tag, prompt_context_temp])

prompt_context_by_speaker

[['speaker_1',
  [" This podcast is supported by the icon school of medicine at Mount Sinai the academic arm of the Mount Sinai health system in New York City and one of America's leading research medical schools. What are researchers working on to advance our understanding of the brain and to improve care for such disorders as depression dementia and drug addiction? To find out we invite you to read a special supplement to Science magazine prepared by icon Mount Sinai in partnership with science. Just visit our website at www.science.org and search for frontiers of medical research -brainscience the icon school of medicine at Mount Sinai. We find a way.",
   "for April 21st. 2023. I'm Sarah crespi first up this week. So many",
   "staff News writer Paul voosin joins me to discuss a study that nearly the number these submarine volcanoes next up how to mammals that spend 90% of their time in the water at any sleep. Jessica Kendall Barr is here to talk about her work exploring the sleep 

In [52]:
#print(str.join("\n", prompt_context_by_speaker[1][1]))

### Submit prompts to GenAI APIs

#### Prediction for the entire transcription

In [53]:
textgen_model = vertexai.preview.language_models.TextGenerationModel.from_pretrained('text-bison@001')

In [54]:
preamble = "Summarize the following content: "

In [55]:
prompt_1 = preamble + "\n\n" + str.join("\n", prompt_context)

In [56]:
response_full = textgen_model.predict(
                    prompt_1,
                    max_output_tokens=1024,
                    temperature=0.4,
                    top_p=0.8,
                    top_k=40,
                )

In [57]:
display(Markdown(str('**Prompt**')))
display(Markdown(str(prompt_1)))
print('\n')
display(Markdown(str('**Transcription Summary**')))
display(Markdown(str(response_full)))

**Prompt**

Summarize the following content: 

 This podcast is supported by the icon school of medicine at Mount Sinai the academic arm of the Mount Sinai health system in New York City and one of America's leading research medical schools. What are researchers working on to advance our understanding of the brain and to improve care for such disorders as depression dementia and drug addiction? To find out we invite you to read a special supplement to Science magazine prepared by icon Mount Sinai in partnership with science. Just visit our website at www.science.org and search for frontiers of medical research -brainscience the icon school of medicine at Mount Sinai. We find a way.
This is the science podcast
for April 21st. 2023. I'm Sarah crespi first up this week. So many
seamounts
staff News writer Paul voosin joins me to discuss a study that nearly the number these submarine volcanoes next up how to mammals that spend 90% of their time in the water at any sleep. Jessica Kendall Barr is here to talk about her work exploring the sleep of elephant seals by capturing their brainwaves as they dive down deep to get some sleep and in a sponsored segment from our custom publishing office assistant editor of custom publishing Jackie oberstalks addiction researchers Eric nessler and Paul Kenny about what researchers have discovered about addiction over the five years and where the field is going. Only about 25% of the ocean floor has been charted or mapped. We don't know where all the big dips like trenches are or the big Peaks like sea mounts. We don't know where those are either today. We have staff News writer Paul vusin. He wrote this week about a study that nearly doubled the count of known seamounts. Hi Paul.
Hello.
Why is the ocean? So mysterious? Why don't we know have more of it mapped? What's the holdup here?
Well, just a lot of water, you know, but oceanographers will always tell you is we know the surface of the Moon or Mars better than we know the ocean which is true. It's just, you know, all that water kind of gets the way of seeing what's down there 4,000 meters 5,000 meters down and the best method we have for doing this is sonar, you know, it's acoustic pings, but that requires expensive ships. So even with Push in recent years to do mapping better. We're only at 25% of the ocean mapped with sonar
your story actually opens with a collision at least the draft that I read. So there are unmapped areas where ships spend time and they can run into sea mounts. That's that's actually a thing that happens.
Well ships usually don't but submarines too.
There we go. That makes it yeah.
So this is a particular Hazard for submarines because you know, a lot of the closest seamounts are closest to the surface are known or their Islands. But yeah, you can even see them kind of underwater. So close enough to the surface with satellite imaging but yeah, there's a couple of famous incidents where the US Navy has run into Uncharted sea amounts including most recently year and a half ago in the South China Sea.
So the new study did not use sonar which is kind of the standard what people might expect for mapping underwater. What technology do they use instead to try to find all these seamounts?
Yeah. So this is building off a technique that's been used for a couple of decades where you have these radar equip satellites that measure the height of the ocean worldwide. These are The Satellites that provide us with sea level rise from climate change, but they can also they can detect changes slope in the water the ocean surface and these can indicate gravity of sea amounts under To kind of bunching up a little bit of water above them. And so with those little slopes these changes in the angle of the water. You can make a pretty pretty good guess of the sea mount and depth of the cement.
So the new study did this worldwide and how many new seamounts were identified or mapped in this research
19,000 over 19,000. And
how many do we know about before?
I think it was about 25,000 we know about four a lot of those with previous kind of versions of this technique. This is just an improvement reflecting that there are more capable satellites that have been up there for, you know, a decade now and you improve the resolution you can improve the number of size of sea mounts you can see so these are especially smaller sea mounts that they've been able to identify now.
What's a smaller seam out? How big would that be?
You know people love to quibble about the definition of it, but usually to be, you know, a proper seam out you need to be these are essentially underwater volcanoes like a kilometer. I are taller.
Okay, it's pretty big but it's still buried under a ton of water. We can detect it by looking at the surface of the water and finding like little changes in the slope. And we got another 19,000 of these females. One thing I'm curious about is is the distribution different and we're basically almost doubling the number of seamounts. Are they cropping up in unexpected places or they denser or more generally randomly distributed.
This is just the the map coming out. They didn't do analyzes on you know, that more of that will come but this has filled in kind of blank spaces. So they're a bunch around Antarctica that weren't visible before at least smaller sea mounts also up in the North Atlantic. These were kind of just blank maps for sea mountains and all the sudden. Oh, hello, they'll appear.
Yeah, these females are volcanoes. So where they are and where they form can tell us something about what's going on with Magma with the cross with tectonic plates.
Yeah. Please have been used in debate. Over hotspots and like mantle plumes of as you know, a lot of them are around mid-ocean ridges right where the tectonic plates are spreading apart and you get magma coming up others are due to hot spots like the Hawaiian chain of islands are your classic chain of sea mount islands and the kind of number of them the volume of them can inform these type of debates
very cool seamount's really they just have so many implications when you first mention this the story in a meeting. I was like Oh, see now it's okay more underwater mountains and it's like no this is also where a ton of sea life congregates and it's like little ecosystems almost like underwater islands of life. So this is going to really change our understanding of that as well.
That's one biologist put it you can't protect these places. If you don't know they're there right now. These are like little skyscrapers of Life. They go up through the water column. Each part of the water column has its own type of Life associated with it the very good for corals because Hard surfaces when you have more of these. Oh, you can find interesting individual ones. You can also kind of get these bigger questions of how interconnected they are. You know, are they kind of isolated pockets evolving distinct life or are they stepping stones that let life skip through the ocean to migrate across
Into the sea mounts. These are all really important results from getting the maps. Right but you actually say in your story that the most important results of this are a better understanding of their effect on the ocean itself. Can you expand on that? Yeah
for a long time. There's been this big debate. So you have this big circulation in the ocean the overturning circulation that moves all the Heat and carbon on Earth and we know why the water goes down and we know why water goes up in like shallow areas because of wind especially an Antarctica but there's been a lot of debate of why it goes up from the abyss like the deepest part of the ocean upward it's dense, you know, why does it go up for a long time those thought to go up evenly distributed but to the mid layer of the ocean but there's been over the past decade research showing that actually it's kind of topography kind of turbulent breaking against topography or wakes created by topography that can allow this denser water to mix upwards and see amounts Famously Walter monk famous oceanographer put at the kind of stirring rods of the ocean or the straws this through the ocean some like that and it's becoming very clear that they could be in a preprint using the old atlas of sea mounts kind of the dominant force of driving the upward circulation.
Wow, so we're going to be able to map this better and then get a better idea of how it interacts with circulation. Once we kind of have a true Count and a true map
how true this is these are still geophysical like people will be like, well, you know, you got to go out and ping it with a acoustic sonar but
is that what's next there needs to be confirmation of these satellite observations with on that the ground but on the water checks,
actually the National geospatial Intelligence Agency, which is partly sponsoring. This work is commissioning sale drone who has these autonomous sailboats that are now starting to carry multi-beam sonars to go out and check some of these look like could be the most hazardous on the This catalog and GA has actually and it's Partners Navy. I have checked out 50% of them already and kind of confirm them.
Oh, wow. All right. Thank you so much Paul.
Yeah, no problem.
Paul Visine as a staff News writer for science. You can find a link to the story. We discussed at science.org slash podcast. Don't touch that phone iPod Alexa. Whatever next up is my interview with Jessica Kendall Barr who had the pleasure of watching seals Slumber for her research. For mammals that live most of their lives in the water or like whales or some seals it's not always easy to grab a nap or sleep deeply hanging out at the surface can make them an easy target for Predators going down deep means no breathing during sleep this week in science, Jessica Kendall bar and colleagues looked into elephant seal sleep and found some unexpected things. We're talk about how they figured it out and what it for sleeping. Hi
Jessica, welcome to the science podcast. Hi. Thank you for having me. Oh sure. So I outlined a few challenges
of sleeping in the ocean if you need to breathe air. Was it a big question then of where they decided to sleep if they spend so much time underwater.
Yes, so we didn't know when they found time to sleep because they basically spend most of their time during these long foraging Dives that go very deep and only maybe one to two minutes at the surface at a time. And what about land? Do they ever just go take
a nap on the beach? Yeah.
So northern elephant seals come on land twice a year once to breed and once to molt and they spend a lot of time sleeping during that time, but that's not the most accurate representation of what their activity budgets are when they're at Sea, right? They don't just sleep twice a year,
right? Yeah. So when we start talking about the challenges of being a sea creature that needs to breathe and sleep. It really just reminds me like about the basic mystery sleep why we need it. How much do need all these different strategies for getting it when you can depending on You live in the environment and you know, how flexible can we be? Can you talk about some of the other marine mammals approaches to sleeping in the ocean whales or dolphins or other kinds of seals? What do we know about them?
You may have heard that dolphins and actually first seals as well can sleep in just half of their brain at a time.
Okay,
that's called a uni hemispheric sleep and that allows them basically to keep one eye open and help monitor Predators while they might be getting the the benefits of sleep.
Yeah for half their brain and then they take a turn on the other side. Yep.
That's that's the idea. So if you had a guess, what would it be like to have
sleep like this hemispheric sleep like a dolphin so
I don't know that I have to guess although we definitely don't do it to the same extent as Dolphins, but there is this documented Effect called the first night effect. So when you go to a new Face, you might just be slightly more aware and there's some evidence that there's a little bit of asymmetry in the degree to which your each of your hemispheres are engaging in slow-wave sleep again. It's probably more like asymmetrical slow wave sleep as opposed to UNI hemispheric slow wave sleep. But this first night effect, you know where you're kind of generally aware of things. You might feel like you've opened some
eyes or I know exactly what you're talking about. Yeah. I hate it. So I don't want to be a dolphin. Yeah. So for this study you were looking at elephant seals. They spend a lot of time out in the water. They spend a lot of time very deep and they hold their breath. They're kind of these extreme divers spending a ton of time underwater. How are you able to see? I'm gonna put quotations around that what they are doing what they're far from Shore and deep underwater. That's definitely a challenge especially since the
the areas where Thing are for the most part pitch black.
Yeah, so
we used basically these sleep monitors that we attached to the seals and then they were able to to take those sleep monitors to see and come back with this gold mine of data about where they went and what they did and we also had sensors that monitor their Motion in three dimensions. Something that I'm really passionate about is this ability to see and sort of experience what it's like to be a seal under underwater. So I've built these tools so that we can create data-driven animations where we see the seals sort of traveling hundreds of meters below the ocean's surface what they're doing with their bodies in terms of the pitch role how they're swimming Behavior might change and frequency and then be able to see these beautiful sleep spirals that they yeah, they do under the ocean surface. Yeah. This is just amazing looking data. It's pretty great. I wish you could show everybody who is listening but they can terribly check out the animation online and look at the figures in the paper. They do a really good job kind of explaining what we're going to try to say, we're gonna try to put it in their ears right now. So in terms of the Sleep monitoring is this what we think of when we you know, somebody's in a sleep study and they have electrodes on their scalp exactly. We use the same sensors that are used in human sleep studies and I actually tried a lot of these methods out on myself and spend some time floating in shallow water and trying to sleep to see if it was working. Alright,
that is so fun. How are you able to put those on elephant seals are pretty big. I guess we should remind people like the males are the ones with the crazy faces, but the females are also very large animals, right? Definitely they're very big and they can be
pretty dangerous when we're working with the animals in order to ensure the safety of our own crew and the Animals they're often sedated and then we'll have the time to work with the animal attach everything make sure there's no flats that are going to create drag for the animal and then we send them off at these basically little head caps that are monitoring sleep and a little Data Logger on the back to store the data that we collect.
So you did this with like a smaller group of elephant seals, we're gonna talk about the larger data set in a minute. And so what you know, let's talk about the patterns that you saw what conclusions were able to draw from the readings out of their brain. And then what their bodies were doing in the water and their depth. What did you figure out about
their sleep patterns? One of the big challenges is I'm trying to interpret nine electrophysiological channels. So that's signals from what the heart's doing what the muscles are doing what the brain is doing. I'm also trying to look at all of these three-dimensional motion sensors and piece together what the animals doing in three-dimensional space. So something that I found myself doing a lot was creating these 3D plots and then I would map one of the variables on to color so I would be able to see if the plot changed color that was a shift in state. So one of the first things that I did is I analyzed the Sleep recordings on their own. So what happens for an animal including us? As we fall asleep and go into slow wave sleep is the signals in your brain. Basically your neurons start to sync up that creates these large slow waves. And then as you transition to REM sleep your brain waves start to sort of transition back to what they look like during waking but you're not awake yet and your heartbeat becomes erratic and often for humans are bodies become paralyzed right that prevents us from acting at our dreams and you know violent behaviors that we might dream of and that keeps us safe in our bed, but you can imagine for a seal at Sea that is becoming paralyzed under the ocean. Yeah, that sounds kind of scary potentially scary. So anyways, so I plotted those colors onto the 3D plot and was able to see these transitions based on color in the three-dimensional plot. And I remember this time when I switched the meaning of color from sleep state to role. So basically whether the animal was on its belly or upside down and I noticed that it didn't really change. They're looked to be the same pattern. So I made sure you know, I was doing my coding correctly and then I found out that around the same time that they're shifting to REM sleep. They're flipping upside down and they're starting to spin in a circle. And I think that's one of the important things that our studies showed is that they're able to sleep and go into slow wave sleep while they're still you know, they might look like they're awake.
They're just gliding and they're they're getting deeper, right?
They're belly down going deeper and then they'll switch to REM sleep flip upside down and that's when they start to do this spiral. So if we were only thinking that they slept during this spirals we would be really misinterpreting what the bigger picture is. Yeah. Is it unusual that they have REM sleep is an ocean mammal, I certainly think so. We haven't recorded sleep in any other wild marine mammals, so I can't tell you for sure how unusual that is, but right I know for sure that the animals that they've recorded. In the lab environment dolphins and fur seals don't seem to exhibit any REM sleep or if they do for seals May exhibit one to ten seconds of REM sleep at a time. But what happens is there head kind of falls under the surface, they start to blow bubbles and then they're like up I gotta breathe.
Right? Right. So that's a and then they're doing the half hemisphere the one hemisphere sleep too, right
exactly. So it seems like maybe that unit hemispheric sleep is sort of replacing in some way the needs of REM sleep which is really interesting for us to understand the function of these different types of sleep in animals in other
mammals such as ourselves, but it sounds like we need to do more in the wild in order to better understand what happens different depths and different situations for these
animals. Definitely. It's possible that some of the good breath holders might be able to exhibit REM
sleep somewhere safe. Yeah, we should talk about how long they're sleeping for because they are they're going on this the slow wave sleep and you can think of it as a slow incline slide into these deep depths now, they're at like 200 meters and they're doing this spiral down with the up and the REM sleep. How long does this process take?
So the animals that we equipped with sleep monitors were juvenile animals with a slightly lower dive capacity. So their average sleep duration was somewhere around five minutes at a time. And those Dives were about 15 to 20 minutes long. I think as long as 25 minutes. And then when we use that data to try to find naps in other data sets with just time and depth. Those animals are adults with larger dive capacities and their Dives were much longer about 30 minutes and they were able to sleep for a grand total of 10 minutes per dive. Yeah,
let's talk about this larger data set. So you took what you knew from these experiments with the while the animals wearing the sensors and you kind of came up with a pattern of what sleep looked like and then you went to another data set where the behavior and the position of elephant seals over a much larger group had been recorded and then you could pick out what looked like sleep from the that data set. How many animals are we talking here? How many sleep sessions are we talking here? We had a subset of
data that had both time depth records and stroking information so we could verify okay. They're actually not stroking during this time. So it it's reasonable to call this five-minute period where they're not moving at all sleep and then the larger data set. Those big as 334 seals which is an incredible data set to work with Dan Costa at UC Santa Cruz, who is my advisor for my PhD has been working for over 25 years to collect time depth records and track these elephant seals as they embark on seven months long migrations. That's just a really amazing opportunity to extrapolate what I'm finding in a small number of seals to this population level when you look at the population.
You see these sleep Dives you see the variation in time kind of depending on you say they're dive capacity. How much sleep do they get in a day on average than if this dive take some 15 minutes and they spend five minutes sleeping. How many times do they do that? What's a day like for an elephant seal the vast majority
of the records are these Dives that go out to see they're called this pelagic foraging strategy where they'll go almost halfway to Japan and back and for those animals, they're sleeping about two hours a day and for the longer trips. It's slightly more and for the shorter trips, it's slightly less. So that's sort of the typical pattern, but then there's also these animals that take a different foraging strategy and they travel up the coast. So they often go to British Columbia or the Aleutian Islands and sort of hug the coast all the way up through Alaska and thereforeaging much deeper. Some of these animals are foraging below 1000 meters. Oh wow deep. Yeah, and then they only perform maybe three or four somewhere between three or four and and 10 forging Dives a day and they spend the rest of the time sleeping. So they sort of flip this pattern and they're sleeping sometimes upwards of 10 hours per day in these naps that just take up most of the day and then they're doing these deep forging Dives. So just shows how important it is to yeah to look at these patterns and not assume anything from a single recording and be able to look at patterns of 334 seals. Yeah. I
love how you call it a sleep scape like looking across the whole population. I mean really this really does like a flexibility Beam patterns which I don't know people don't really seem to have that much flexibility. How does their heart rate fit in with all of this? Is that also kind of on the extreme end of things like flexible because they're diving sleeping underwater expending a lot of energy swimming around
it can really depend on the age of the animal and sort of how much they've built up this mammalian dive response to lower their heart rate and they're diving but in my records I recorded heart rates that were as high as over 200 beats per minute and as low as five feets per minute those recordings of five beats per minute happened after they potentially found a killer whale out at Sea and they lowered their heart rate immediately and sort of Dove back down. You can see it in the dive profile too. They got pretty close to the surface and then they decide
nope. I think that really again points out the value of animals in the Build doing these different activities having all these different interactions. So yeah, I think these studies
of sleep are really important so that we can figure out how where and when these animals are sleeping in the wild and we can use that information to better manage and protect their critical resting habitats. Thank you so much Jessica.
Yeah, Jessica, Kendall Barr is the Schmidt AI science postdoctoral fellow at the scripts institution of oceanography at UC San Diego. You can find a link to the paper we discussed. It's science.org slash podcast up next. We have a custom segment sponsored by the icon school of medicine at Mount Sinai. Custom publishing assistant editor Jackie Oberst chats with Eric nessler and Paul Kenny two experts on addiction about the latest research in the field.
Hello
to our podcast listeners and welcome to the custom sponsor interview from the science triple A S custom publishing office and brought to you by the icon school of medicine at Mount Sinai. My name is Jackie Oberst and I'm assistant editor for custom publishing at science. Whether it's a problem with alcohol opioids cocaine or any other substance addiction or substance. Use disorder is a chronic mental health condition that kills hundreds of thousands of Americans every year and impacts millions of lives addictions can destroy marriages friendships and careers and threaten a person's basic health and safety. It is a medical problem that needs Medical Solutions today. I'm very pleased to welcome to renowned experts on addiction. They are co-authors with several colleagues on an upcoming article about the science of addiction in a neuroscience supplement of science that will come out in June Dr. Eric nessler who is the Nash family professor of Neuroscience director of the Friedman brain Institute dean for academic Affairs at The Icon school of medicine Mount Sinai and chief officer of the Sinai Health System his laboratory studies the molecular mechanisms of drug addiction and depression in animal models. We also have Dr. Paul Kenny who is the ward Coleman's professor and chair of the Nash family Department of Neuroscience as well as a director of the drug Discovery Institute at The Icon school of medicine at Mount Sinai his multidisciplinary research involves the study of Behavioral paradigms physiological analyzes and the molecular underpinnings of neuro behavioral disorders such as schizophrenia and drug addiction Eric and Paul. Thank you so much for taking the time to talk with me today Eric. I'd like to orient our listeners to the topic how to researchers Define addiction
researchers Define addiction the same way clinicians do and this is one of the major gaps and now we're knowledge addiction like all psychiatric syndrome and only be diagnosed by talking to a person or their family members and finding out what types abnormal behaviors they exhibit no blood test. No genetic test. No brain scan can be used. Diagnose
addiction
Paul, could you please also weigh in
well addictions are very tricky word. I think the way that addictionologists would Define addiction is a compulsive behavior that persists despite clear evidence suggesting that the behavior should stop and the behavior is directed towards obtaining drug abuse
and now I'd like to focus on why this is an important issue. What is the impact? That addiction has on Society
on society addiction has a devastating consequence. I think we all know about the opioid epidemic that script the us over the past maybe 10 years. It's a leading cause of premature death here in the United States and elsewhere in the world and it's not just death that is a negative consequence of illicit drug use, I mean the impact really on every aspect of life and Society is marked
Eric our addiction related deaths on the rise. If so, why
yes, so we we've seen a an epidemic of addiction related deaths and I really want to underscore this before the pandemic. It was reported that we about 70,000 Americans died every year of a drug overdose and the vast majority of that being unintentional. These are not people who are looking or hurt or harm themselves. These are people who die accidentally by taking too much drug that number has increased dramatically since the pandemic. So the last data available would suggest that 100,000 Americans Die each year now from drug overdose and I'd like to put that in some perspective. I was a teenager young adult during the Vietnam War era I generation was defined by that war 58,000 American combat troops died during a 15-year course of that war and my generation was torn up over it yet. Here. We are in the United States today losing 100,000 Americans every year because of addiction and we don't seem to be able to Marshal the resources to address it
Paul your opinion on this, please
there's many reasons for increased instance of that that we're seeing. One of the major reasons is related to just the excessive amounts of opioids are consumed in the United States. The greatest quantities of opioid drugs are by far consumed when the United States or does the magnitude above oh God consumption and other parts of the world, but it's not just opioids. We're seeing a real clear spike use of other list drugs like More stimulants cocaine of course being the example of that amphetamines metaphetamine use is also on the increase and those drugs have devastating consequences as well.
What do we know about the science of addiction that we didn't know five years ago.
So several areas of advances have been made first We Now understand what it is about a chemical substance that makes it able to cause addiction and a vulnerable person drugs of abuse all share the ability to act on the brains reward Pathways reward Pathways or parts of the brain that are very old from an evolutionary point of view and they develop to regulate an individual's responses to rewards in the environment our Behavior shaped by rewards the availability of food and water sex social interaction and our actions are being continually refined in response to these cues and the environment when a person takes a drug of abuse person has the experience as if they've had the most rewarding experience possible without actually having something useful happening to them no food. No, Associated with it the power and Persistence of these actions of drugs on the brain reward circuitry triggers chemical changes in the brain that basically corrupt the brain's ability to analyze rewards now an individual who's addicted is not rewarded by natural things things that most of us are rewarded by but instead require the sledgehammer effects of a drug of abuse in order to feel that natural reward and that is one of the reasons why people with addictions are driven so strongly to take drugs because this is the only way for their brains for themselves to feel normal in addition to identifying parts of the brain that regulate these responses to drugs of abuse. We've also begun to understand the chemical change is that drugs produce in those brain regions to cause an addiction and for that much of the effort has focused on molecular or biology changes in the ability of certain genes within nerve cells in these brain reward regions Their protein products and somehow these changes in gene expression as we would call it drive addiction Behavior
Paul your thoughts please
we now are in a position where we can apply really nice tools to understand the most fundamental actions of drugs abuse in the brain, you know, the molecular cellular circuit level. Also, even the underlying genetics what kinds of Gene variants are we born with them may influence the likelihood that you'll use drugs if you use them, they'll go off and develop a habit and the difficulty that you will have quitting
so applications Eric. What are the most promising directions and future research and treatments.
There are some medications that can be quite effective. So in the case of opioid addiction, we are fortunate to have treatments like methadone and buprenorphine the brand name for buprenorphine with a co-medication is called Suboxone and methadone and Suboxone can be extremely effective and I urge your listeners to check out a hul Through series called dopsec which was really an excellent depiction. First of what opioid addiction can be like how it can attack anybody regardless of their station in life. But it also depicted quite nicely that when people are given the right kinds of treatments like Suboxone. They can really do quite well and begin to recover toward a normal life Paul. You're a piece, please for the most promising Trends in the treatment of drug addictions the fact that we're now actually seeing compounds Advanced through the preclinical development Pipeline and into human clinical trials. And without those types of data. Of course, we won't identify new therapeutic. Also, what if those kind of data we won't know from moving the right direction using the right tools and thinking the right way. So we need those types of human experiments. If you will help guide the preclinical drug development and the likelihood that we can generate not just one therapeutic but the whole Armory a Therapeutics that can address well as a very complex syndrome of Behavioral abnormality
behavioral therapies can be effective interventions for substance use disorders all what do we now know about the biological mechanisms of action of Behavioral therapies,
really surprisingly little I think that's an area of research in our field really would benefit from a lot more attention. You're absolutely right. In fact, even the most effective therapeutic is about as effective as behavioral intervention and the best way currently of treating someone who suffering substance use disorder is Therapeutic and kind of compound that's beneficial buprenorphine being an example and behavioral therapy combined. Well, that's the case. We really don't know if I had to guess I would suggested something around the fact that humans are social animals and that social rewards are so critically important for us as a species and that the reward circuitries that are co-opted by drugs abuse. Some of the Great Lakes are likely involved in social award-related behaviors
Eric your Thoughts, please
behavioral therapies are the Mainstay for addiction treatment for the majority of people behavioral therapies, or what are available and their effective in some people over time. But again with very high rates of relapse an 80% chance of relapse within a year of abstinence a person would go back to behavioral treatment and the cycle continues again, and again and what you hear from so many patients and family members is that a loved one has been in treatment repeatedly and still as at high risk of relapse, so keep hope because there is always hope and eventually actually most people do kick the habit
Eric and Paul. It's been a real pleasure having this opportunity. Thank you both for joining us. Our thanks to the icon school of medicine at Mount Sinai for sponsoring this interview. This podcast has been edited and condensed for length by Erica Burke director and Senior editor of custom publishing and me Jackie Oberst. Thank you for listening. And that concludes this edition of the science podcast. If you have any comments or suggestions write to us at science podcast at aaas.org. You can listen to the show on our website science.org/podcast or search for Science magazine on any podcasting app. This show was edited by me Sarah Presby and Kevin MacLean with production help from Prodigy. Jeffrey cook compose the music on behalf of Science, and it's publisher triple AAS. Thanks for joining us.

**Transcription Summary**

#### Prediction for the transcription by speaker

In [58]:
preamble = "Summarize the following content in 2-3 sentences: "

In [59]:
for prompt in prompt_context_by_speaker:
    prompt_n = preamble + "\n\n" + str.join("\n", prompt[1])
    response_speaker = textgen_model.predict(
                    prompt_n,
                    max_output_tokens=1024,
                    temperature=0.4,
                    top_p=0.8,
                    top_k=40,
                )
    display(Markdown(str('**Prompt - {}**'.format(prompt[0]))))
    display(Markdown(str(prompt_n)))
    print('\n')
    display(Markdown(str('**Transcription Summary**')))
    display(Markdown(str(response_speaker)))
    print('------------------------')



**Prompt - speaker_1**

Summarize the following content in 2-3 sentences: 

 This podcast is supported by the icon school of medicine at Mount Sinai the academic arm of the Mount Sinai health system in New York City and one of America's leading research medical schools. What are researchers working on to advance our understanding of the brain and to improve care for such disorders as depression dementia and drug addiction? To find out we invite you to read a special supplement to Science magazine prepared by icon Mount Sinai in partnership with science. Just visit our website at www.science.org and search for frontiers of medical research -brainscience the icon school of medicine at Mount Sinai. We find a way.
for April 21st. 2023. I'm Sarah crespi first up this week. So many
staff News writer Paul voosin joins me to discuss a study that nearly the number these submarine volcanoes next up how to mammals that spend 90% of their time in the water at any sleep. Jessica Kendall Barr is here to talk about her work exploring the sleep of elephant seals by capturing their brainwaves as they dive down deep to get some sleep and in a sponsored segment from our custom publishing office assistant editor of custom publishing Jackie oberstalks addiction researchers Eric nessler and Paul Kenny about what researchers have discovered about addiction over the five years and where the field is going. Only about 25% of the ocean floor has been charted or mapped. We don't know where all the big dips like trenches are or the big Peaks like sea mounts. We don't know where those are either today. We have staff News writer Paul vusin. He wrote this week about a study that nearly doubled the count of known seamounts. Hi Paul.
Why is the ocean? So mysterious? Why don't we know have more of it mapped? What's the holdup here?
your story actually opens with a collision at least the draft that I read. So there are unmapped areas where ships spend time and they can run into sea mounts. That's that's actually a thing that happens.
There we go. That makes it yeah.
So the new study did not use sonar which is kind of the standard what people might expect for mapping underwater. What technology do they use instead to try to find all these seamounts?
So the new study did this worldwide and how many new seamounts were identified or mapped in this research
how many do we know about before?
What's a smaller seam out? How big would that be?
Okay, it's pretty big but it's still buried under a ton of water. We can detect it by looking at the surface of the water and finding like little changes in the slope. And we got another 19,000 of these females. One thing I'm curious about is is the distribution different and we're basically almost doubling the number of seamounts. Are they cropping up in unexpected places or they denser or more generally randomly distributed.
Yeah, these females are volcanoes. So where they are and where they form can tell us something about what's going on with Magma with the cross with tectonic plates.
very cool seamount's really they just have so many implications when you first mention this the story in a meeting. I was like Oh, see now it's okay more underwater mountains and it's like no this is also where a ton of sea life congregates and it's like little ecosystems almost like underwater islands of life. So this is going to really change our understanding of that as well.
Into the sea mounts. These are all really important results from getting the maps. Right but you actually say in your story that the most important results of this are a better understanding of their effect on the ocean itself. Can you expand on that? Yeah
Wow, so we're going to be able to map this better and then get a better idea of how it interacts with circulation. Once we kind of have a true Count and a true map
is that what's next there needs to be confirmation of these satellite observations with on that the ground but on the water checks,
Oh, wow. All right. Thank you so much Paul.
Paul Visine as a staff News writer for science. You can find a link to the story. We discussed at science.org slash podcast. Don't touch that phone iPod Alexa. Whatever next up is my interview with Jessica Kendall Barr who had the pleasure of watching seals Slumber for her research. For mammals that live most of their lives in the water or like whales or some seals it's not always easy to grab a nap or sleep deeply hanging out at the surface can make them an easy target for Predators going down deep means no breathing during sleep this week in science, Jessica Kendall bar and colleagues looked into elephant seal sleep and found some unexpected things. We're talk about how they figured it out and what it for sleeping. Hi
of sleeping in the ocean if you need to breathe air. Was it a big question then of where they decided to sleep if they spend so much time underwater.
a nap on the beach? Yeah.
right? Yeah. So when we start talking about the challenges of being a sea creature that needs to breathe and sleep. It really just reminds me like about the basic mystery sleep why we need it. How much do need all these different strategies for getting it when you can depending on You live in the environment and you know, how flexible can we be? Can you talk about some of the other marine mammals approaches to sleeping in the ocean whales or dolphins or other kinds of seals? What do we know about them?
Okay,
Yeah for half their brain and then they take a turn on the other side. Yep.
sleep like this hemispheric sleep like a dolphin so
eyes or I know exactly what you're talking about. Yeah. I hate it. So I don't want to be a dolphin. Yeah. So for this study you were looking at elephant seals. They spend a lot of time out in the water. They spend a lot of time very deep and they hold their breath. They're kind of these extreme divers spending a ton of time underwater. How are you able to see? I'm gonna put quotations around that what they are doing what they're far from Shore and deep underwater. That's definitely a challenge especially since the
Yeah, so
that is so fun. How are you able to put those on elephant seals are pretty big. I guess we should remind people like the males are the ones with the crazy faces, but the females are also very large animals, right? Definitely they're very big and they can be
So you did this with like a smaller group of elephant seals, we're gonna talk about the larger data set in a minute. And so what you know, let's talk about the patterns that you saw what conclusions were able to draw from the readings out of their brain. And then what their bodies were doing in the water and their depth. What did you figure out about
They're just gliding and they're they're getting deeper, right?
Right? Right. So that's a and then they're doing the half hemisphere the one hemisphere sleep too, right
mammals such as ourselves, but it sounds like we need to do more in the wild in order to better understand what happens different depths and different situations for these
sleep somewhere safe. Yeah, we should talk about how long they're sleeping for because they are they're going on this the slow wave sleep and you can think of it as a slow incline slide into these deep depths now, they're at like 200 meters and they're doing this spiral down with the up and the REM sleep. How long does this process take?
let's talk about this larger data set. So you took what you knew from these experiments with the while the animals wearing the sensors and you kind of came up with a pattern of what sleep looked like and then you went to another data set where the behavior and the position of elephant seals over a much larger group had been recorded and then you could pick out what looked like sleep from the that data set. How many animals are we talking here? How many sleep sessions are we talking here? We had a subset of
You see these sleep Dives you see the variation in time kind of depending on you say they're dive capacity. How much sleep do they get in a day on average than if this dive take some 15 minutes and they spend five minutes sleeping. How many times do they do that? What's a day like for an elephant seal the vast majority
love how you call it a sleep scape like looking across the whole population. I mean really this really does like a flexibility Beam patterns which I don't know people don't really seem to have that much flexibility. How does their heart rate fit in with all of this? Is that also kind of on the extreme end of things like flexible because they're diving sleeping underwater expending a lot of energy swimming around
nope. I think that really again points out the value of animals in the Build doing these different activities having all these different interactions. So yeah, I think these studies
Yeah, Jessica, Kendall Barr is the Schmidt AI science postdoctoral fellow at the scripts institution of oceanography at UC San Diego. You can find a link to the paper we discussed. It's science.org slash podcast up next. We have a custom segment sponsored by the icon school of medicine at Mount Sinai. Custom publishing assistant editor Jackie Oberst chats with Eric nessler and Paul Kenny two experts on addiction about the latest research in the field.
to our podcast listeners and welcome to the custom sponsor interview from the science triple A S custom publishing office and brought to you by the icon school of medicine at Mount Sinai. My name is Jackie Oberst and I'm assistant editor for custom publishing at science. Whether it's a problem with alcohol opioids cocaine or any other substance addiction or substance. Use disorder is a chronic mental health condition that kills hundreds of thousands of Americans every year and impacts millions of lives addictions can destroy marriages friendships and careers and threaten a person's basic health and safety. It is a medical problem that needs Medical Solutions today. I'm very pleased to welcome to renowned experts on addiction. They are co-authors with several colleagues on an upcoming article about the science of addiction in a neuroscience supplement of science that will come out in June Dr. Eric nessler who is the Nash family professor of Neuroscience director of the Friedman brain Institute dean for academic Affairs at The Icon school of medicine Mount Sinai and chief officer of the Sinai Health System his laboratory studies the molecular mechanisms of drug addiction and depression in animal models. We also have Dr. Paul Kenny who is the ward Coleman's professor and chair of the Nash family Department of Neuroscience as well as a director of the drug Discovery Institute at The Icon school of medicine at Mount Sinai his multidisciplinary research involves the study of Behavioral paradigms physiological analyzes and the molecular underpinnings of neuro behavioral disorders such as schizophrenia and drug addiction Eric and Paul. Thank you so much for taking the time to talk with me today Eric. I'd like to orient our listeners to the topic how to researchers Define addiction
Paul, could you please also weigh in
and now I'd like to focus on why this is an important issue. What is the impact? That addiction has on Society
Eric our addiction related deaths on the rise. If so, why
Paul your opinion on this, please
What do we know about the science of addiction that we didn't know five years ago.
Paul your thoughts please
so applications Eric. What are the most promising directions and future research and treatments.
behavioral therapies can be effective interventions for substance use disorders all what do we now know about the biological mechanisms of action of Behavioral therapies,
Eric your Thoughts, please
Eric and Paul. It's been a real pleasure having this opportunity. Thank you both for joining us. Our thanks to the icon school of medicine at Mount Sinai for sponsoring this interview. This podcast has been edited and condensed for length by Erica Burke director and Senior editor of custom publishing and me Jackie Oberst. Thank you for listening. And that concludes this edition of the science podcast. If you have any comments or suggestions write to us at science podcast at aaas.org. You can listen to the show on our website science.org/podcast or search for Science magazine on any podcasting app. This show was edited by me Sarah Presby and Kevin MacLean with production help from Prodigy. Jeffrey cook compose the music on behalf of Science, and it's publisher triple AAS. Thanks for joining us.

**Transcription Summary**

The podcast discussed 3 topics:
1) The number of seamounts (submarine volcanoes) has been nearly doubled by a new study.
2) Elephant seals sleep in the water by diving deep and taking turns sleeping with one half of their brain at a time.
3) Addiction is a chronic mental health condition that kills hundreds of thousands of Americans every year. Researchers are studying the science of addiction to find new treatments.

------------------------


...

**Prompt - speaker_4**

Summarize the following content in 2-3 sentences: 

researchers Define addiction the same way clinicians do and this is one of the major gaps and now we're knowledge addiction like all psychiatric syndrome and only be diagnosed by talking to a person or their family members and finding out what types abnormal behaviors they exhibit no blood test. No genetic test. No brain scan can be used. Diagnose
well addictions are very tricky word. I think the way that addictionologists would Define addiction is a compulsive behavior that persists despite clear evidence suggesting that the behavior should stop and the behavior is directed towards obtaining drug abuse
on society addiction has a devastating consequence. I think we all know about the opioid epidemic that script the us over the past maybe 10 years. It's a leading cause of premature death here in the United States and elsewhere in the world and it's not just death that is a negative consequence of illicit drug use, I mean the impact really on every aspect of life and Society is marked
yes, so we we've seen a an epidemic of addiction related deaths and I really want to underscore this before the pandemic. It was reported that we about 70,000 Americans died every year of a drug overdose and the vast majority of that being unintentional. These are not people who are looking or hurt or harm themselves. These are people who die accidentally by taking too much drug that number has increased dramatically since the pandemic. So the last data available would suggest that 100,000 Americans Die each year now from drug overdose and I'd like to put that in some perspective. I was a teenager young adult during the Vietnam War era I generation was defined by that war 58,000 American combat troops died during a 15-year course of that war and my generation was torn up over it yet. Here. We are in the United States today losing 100,000 Americans every year because of addiction and we don't seem to be able to Marshal the resources to address it
there's many reasons for increased instance of that that we're seeing. One of the major reasons is related to just the excessive amounts of opioids are consumed in the United States. The greatest quantities of opioid drugs are by far consumed when the United States or does the magnitude above oh God consumption and other parts of the world, but it's not just opioids. We're seeing a real clear spike use of other list drugs like More stimulants cocaine of course being the example of that amphetamines metaphetamine use is also on the increase and those drugs have devastating consequences as well.
So several areas of advances have been made first We Now understand what it is about a chemical substance that makes it able to cause addiction and a vulnerable person drugs of abuse all share the ability to act on the brains reward Pathways reward Pathways or parts of the brain that are very old from an evolutionary point of view and they develop to regulate an individual's responses to rewards in the environment our Behavior shaped by rewards the availability of food and water sex social interaction and our actions are being continually refined in response to these cues and the environment when a person takes a drug of abuse person has the experience as if they've had the most rewarding experience possible without actually having something useful happening to them no food. No, Associated with it the power and Persistence of these actions of drugs on the brain reward circuitry triggers chemical changes in the brain that basically corrupt the brain's ability to analyze rewards now an individual who's addicted is not rewarded by natural things things that most of us are rewarded by but instead require the sledgehammer effects of a drug of abuse in order to feel that natural reward and that is one of the reasons why people with addictions are driven so strongly to take drugs because this is the only way for their brains for themselves to feel normal in addition to identifying parts of the brain that regulate these responses to drugs of abuse. We've also begun to understand the chemical change is that drugs produce in those brain regions to cause an addiction and for that much of the effort has focused on molecular or biology changes in the ability of certain genes within nerve cells in these brain reward regions Their protein products and somehow these changes in gene expression as we would call it drive addiction Behavior
we now are in a position where we can apply really nice tools to understand the most fundamental actions of drugs abuse in the brain, you know, the molecular cellular circuit level. Also, even the underlying genetics what kinds of Gene variants are we born with them may influence the likelihood that you'll use drugs if you use them, they'll go off and develop a habit and the difficulty that you will have quitting
There are some medications that can be quite effective. So in the case of opioid addiction, we are fortunate to have treatments like methadone and buprenorphine the brand name for buprenorphine with a co-medication is called Suboxone and methadone and Suboxone can be extremely effective and I urge your listeners to check out a hul Through series called dopsec which was really an excellent depiction. First of what opioid addiction can be like how it can attack anybody regardless of their station in life. But it also depicted quite nicely that when people are given the right kinds of treatments like Suboxone. They can really do quite well and begin to recover toward a normal life Paul. You're a piece, please for the most promising Trends in the treatment of drug addictions the fact that we're now actually seeing compounds Advanced through the preclinical development Pipeline and into human clinical trials. And without those types of data. Of course, we won't identify new therapeutic. Also, what if those kind of data we won't know from moving the right direction using the right tools and thinking the right way. So we need those types of human experiments. If you will help guide the preclinical drug development and the likelihood that we can generate not just one therapeutic but the whole Armory a Therapeutics that can address well as a very complex syndrome of Behavioral abnormality
really surprisingly little I think that's an area of research in our field really would benefit from a lot more attention. You're absolutely right. In fact, even the most effective therapeutic is about as effective as behavioral intervention and the best way currently of treating someone who suffering substance use disorder is Therapeutic and kind of compound that's beneficial buprenorphine being an example and behavioral therapy combined. Well, that's the case. We really don't know if I had to guess I would suggested something around the fact that humans are social animals and that social rewards are so critically important for us as a species and that the reward circuitries that are co-opted by drugs abuse. Some of the Great Lakes are likely involved in social award-related behaviors
behavioral therapies are the Mainstay for addiction treatment for the majority of people behavioral therapies, or what are available and their effective in some people over time. But again with very high rates of relapse an 80% chance of relapse within a year of abstinence a person would go back to behavioral treatment and the cycle continues again, and again and what you hear from so many patients and family members is that a loved one has been in treatment repeatedly and still as at high risk of relapse, so keep hope because there is always hope and eventually actually most people do kick the habit

**Transcription Summary**

Addiction is a complex problem with devastating consequences.
Researchers are making progress in understanding the brain mechanisms of addiction and developing new treatments.
However, more research is needed to develop more effective treatments and to understand why relapse is so common.

------------------------


### Functions - for future reference

In [ ]:
def mp3_to_wav(audio_file_name):
    if audio_file_name.split('.')[1] == 'mp3':    
        sound = AudioSegment.from_mp3(audio_file_name)
        audio_file_name = audio_file_name.split('.')[0] + '.wav'
        sound.export(audio_file_name, format="wav")

In [ ]:
def frame_rate_channel(audio_file_name):
    with wave.open(audio_file_name, "rb") as wave_file:
        frame_rate = wave_file.getframerate()
        channels = wave_file.getnchannels()
        return frame_rate,channels

In [ ]:
def stereo_to_mono(audio_file_name):
    sound = AudioSegment.from_wav(audio_file_name)
    sound = sound.set_channels(1)
    sound.export(audio_file_name, format="wav")